In [1]:
import numpy as np
import pandas as pd
import math
import sys, os
#import seaborn as sns
#from scipy import stats
#from pathlib import Path
#import matplotlib.pyplot as plt
#from sklearn.model_selection import KFold
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
#from sklearn.metrics import mean_squared_error
#from sklearn.metrics import mean_squared_error
#from sklearn.preprocessing import MinMaxScaler
#from sklearn.datasets import fetch_california_housing
#import math
from tqdm import tqdm
from sklearn.feature_extraction.text import CountVectorizer
import optuna
from optuna.samplers import TPESampler
#import lightgbm as lbgm
#from xgboost import XGBRegressor
#import xgboost as xgb
from catboost import CatBoostRegressor
#from lightgbm.sklearn import lbgmRegressor
#from sklearn.ensemble import RandomForestRegressor
import pickle
from sklearn.metrics import roc_curve, auc
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import roc_auc_score
import matplotlib.pyplot as plt
import mplcyberpunk
import seaborn as sns

In [2]:
train_time = 1 * 60 * 60
objective = 'catregressor'

In [3]:
sys.path.append(os.path.realpath('..'))

In [4]:
train_df = pd.read_csv(r"..\data\train.csv", index_col=0)
test_df = pd.read_csv(r"..\data\test.csv", index_col=0)
sample_sub = pd.read_csv(r"..\data\sample_submission.csv", index_col=0)

In [5]:
features = ['V1', 'V2', 'V3', 'V4', 'V5', 'V6', 'V7', 'V8', 'V9', 'V10',
       'V11', 'V12', 'V13', 'V14', 'V15', 'V16', 'V17', 'V18', 'V19', 'V20',
       'V21', 'V22', 'V23', 'V24', 'V25', 'V26', 'V27', 'V28', 'Amount']
target = ['Class']

In [6]:
np.unique(train_df[target], return_counts=True)

(array([0, 1], dtype=int64), array([218660,    469], dtype=int64))

In [7]:
train_df[features] = train_df[features].apply(lambda iterator: ((iterator.max() - iterator)/(iterator.max() - iterator.min())).round(2))
test_df[features] = test_df[features].apply(lambda iterator: ((iterator.max() - iterator)/(iterator.max() - iterator.min())).round(2))

In [8]:
np.unique(train_df[target], return_counts=True)

(array([0, 1], dtype=int64), array([218660,    469], dtype=int64))

In [9]:
scaler = MinMaxScaler().fit(train_df[features])
X = scaler.transform(train_df[features])
X_test = scaler.transform(test_df[features])

scaler = MinMaxScaler().fit(train_df[target])
Y = scaler.transform(train_df[target])

In [10]:
RANDOM_STATE = 12 
FOLDS = 5
param_grid_history = {}

def render_model(param_grid):
    reg = CatBoostRegressor(iterations=20000,
                            **param_grid,
                            bootstrap_type='Bernoulli',
                            grow_policy='SymmetricTree',
                            #loss_function='Logloss',
                            eval_metric='AUC',
                            task_type="GPU",
                            random_state=1,)
    return reg
    
def train_model(reg, X_train, y_train, X_valid, y_valid):
    reg.fit(X_train, y_train, eval_set=(X_valid, y_valid), early_stopping_rounds=100, verbose=1000)

    preds = reg.predict(train_df[features])
    fpr, tpr, _ = roc_curve(train_df[target], preds)
    roc_auc = auc(fpr, tpr)
    return reg, roc_auc

def objective_v2(trial):
    scores = []
    param_grid = {
        'depth': trial.suggest_int('depth', 3, 6),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.9),
        #'rsm': trial.suggest_float('rsm', 0.001, 0.9),
        #'subsample': trial.suggest_float('subsample', 0.1, 1),
        #'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 1, 100), 
        #'one_hot_max_size': trial.suggest_int('one_hot_max_size', 1, 100), 
        #'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 0.01, 20),
        'reg_lambda': trial.suggest_int('reg_lambda', 30, 100), 
        #'random_strength': trial.suggest_float('random_strength', 0.001, 0.9),
        #'colsample_bylevel': trial.suggest_float('colsample_bylevel', 0.001, 0.9),
    } 
        
    skf = StratifiedKFold(n_splits=FOLDS, shuffle=True, random_state=RANDOM_STATE)
    for z in range(10):
        for fold, (train_idx, valid_idx) in enumerate(skf.split(X, Y)):
            print(10*"=", f"Fold={fold+1}", 10*"=")
            X_train, X_valid = train_df.iloc[train_idx][features], train_df.iloc[valid_idx][features]
            y_train , y_valid = train_df[target].iloc[train_idx] , train_df[target].iloc[valid_idx] 

            reg = render_model(param_grid)
            reg, roc_auc = train_model(reg, X_train, y_train, X_valid, y_valid)

            scores.append(roc_auc)
    mean_scores = np.mean(scores)
    param_grid_history[mean_scores] = param_grid

    return mean_scores

In [11]:
RANDOM_STATE = 12 
FOLDS = 5
param_grid_history = {}
best_auc = 0


def objective_v3(trial):
    global best_auc
    oof = np.zeros(len(X))
    scores = []
    param_grid = {
        'depth': trial.suggest_int('depth', 3, 8),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.9),
        #'rsm': trial.suggest_float('rsm', 0.001, 0.9),
        #'subsample': trial.suggest_float('subsample', 0.1, 1),
        #'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 1, 100), 
        #'one_hot_max_size': trial.suggest_int('one_hot_max_size', 1, 100), 
        #'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 0.01, 20),
        'reg_lambda': trial.suggest_int('reg_lambda', 1, 5), 
        #'random_strength': trial.suggest_float('random_strength', 0.001, 0.9),
        #'colsample_bylevel': trial.suggest_float('colsample_bylevel', 0.001, 0.9),
    } 
        
    skf = StratifiedKFold(n_splits=FOLDS, shuffle=True, random_state=RANDOM_STATE)
    for z in range(10):
        for fold, (train_idx, valid_idx) in enumerate(skf.split(X, Y)):
            print(10*"=", f"Fold={fold+1}", 10*"=")
            X_train, X_valid = train_df.iloc[train_idx][features], train_df.iloc[valid_idx][features]
            y_train , y_valid = train_df[target].iloc[train_idx] , train_df[target].iloc[valid_idx] 

            reg = CatBoostRegressor(iterations=20000,
                                **param_grid,
                                bootstrap_type='Bernoulli',
                                grow_policy='SymmetricTree',

                                #loss_function='Logloss',
                                eval_metric='AUC',
                                task_type="GPU",
                                random_state=1,)

            reg.fit(X_train, y_train, eval_set=(X_valid, y_valid), early_stopping_rounds=100, verbose=1000)

            oof[valid_idx] = reg.predict(X_valid)

        roc_auc = roc_auc_score(Y, oof)

        if roc_auc > best_auc:
            best_auc = roc_auc
            train_final_preds = reg.predict(train_df[features])
            test_final_preds = reg.predict(test_df[features])
            train_submission = pd.DataFrame(data={'id': train_df.index, target[0]: train_final_preds})
            train_submission.to_csv(fr'rendered_data/{objective}_train_submission.csv', index=False)
            test_submission = pd.DataFrame(data={'id': test_df.index, target[0]: test_final_preds})
            test_submission.to_csv(fr'rendered_data/{objective}_test_submission.csv', index=False)
    
    param_grid_history[roc_auc] = param_grid

    return roc_auc

In [ ]:
study = optuna.create_study(direction='maximize', sampler=TPESampler(), study_name=objective)
study.optimize(objective_v3, n_trials=1000)

[I 2023-01-28 13:14:32,708] A new study created in memory with name: catregressor


========== Fold=1 ==========


Default metric period is 5 because AUC is/are not implemented for GPU
AUC is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time


0:	test: 0.6463608	best: 0.6463608 (0)	total: 5.72ms	remaining: 1m 54s
bestTest = 0.8126811079
bestIteration = 31
Shrink model to first 32 iterations.
========== Fold=2 ==========


Default metric period is 5 because AUC is/are not implemented for GPU
AUC is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time


...

0:	test: 0.6639060	best: 0.6639060 (0)	total: 6.67ms	remaining: 2m 13s
bestTest = 0.7925420015
bestIteration = 351
Shrink model to first 352 iterations.
========== Fold=5 ==========


Default metric period is 5 because AUC is/are not implemented for GPU
AUC is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time


0:	test: 0.6891206	best: 0.6891206 (0)	total: 7.54ms	remaining: 2m 30s
bestTest = 0.8364903926
bestIteration = 101
Shrink model to first 102 iterations.
========== Fold=1 ==========


Default metric period is 5 because AUC is/are not implemented for GPU
AUC is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time


0:	test: 0.6215412	best: 0.6215412 (0)	total: 6.44ms	remaining: 2m 8s


In [ ]:
parm_grid_bytes = pickle.dumps(param_grid_history)
with open(f"rendered_data/{objective}_bytes.hex", "wb") as binary_file:
    binary_file.write(parm_grid_bytes)

In [ ]:
param_grid_history = {}
with open(f"rendered_data/{objective}_bytes.hex", "rb") as input_file:
    param_grid_history = pickle.load(input_file)

In [ ]:
def train(param_grid):
    reg = CatBoostRegressor(iterations=20000,
                        **param_grid,
                        bootstrap_type='Bernoulli',
                        grow_policy='SymmetricTree',
                        #loss_function='Logloss',
                        eval_metric='AUC',
                        task_type="GPU",
                        random_state=1,)
    
    X_train, X_valid, y_train, y_valid = train_test_split(X, Y, test_size=0.20)
    
    reg.fit(X_train, y_train, eval_set=(X_valid, y_valid), early_stopping_rounds=100, verbose=1000)
    
    return reg

percent = math.ceil(len(param_grid_history.keys()) * .1)
top = sorted(list(param_grid_history.keys()))[-percent:]

train_preds = []
test_preds = []
for key in tqdm(top):
    model = train(param_grid_history[key])
    train_preds.append(model.predict(train_df[features]))
    test_preds.append(model.predict(test_df[features]))

train_final_preds = np.stack(train_preds).mean(0)
test_final_preds = np.stack(test_preds).mean(0)

In [ ]:
plt.style.use("cyberpunk")

histplot_hyperparams = {
        'alpha':0.4,
        'stat':'percent',
        'bins':100
    }

n_cols = 1
n_rows = 1
cell_with_dim = 6
cell_height_dim = 3

fig, ax = plt.subplots(n_rows, n_cols, figsize=(n_cols * cell_with_dim, n_rows * cell_height_dim))

sns.histplot(train_final_preds, ax=ax, **histplot_hyperparams)
#sns.histplot(train_df[target], ax=ax, **histplot_hyperparams)

mplcyberpunk.make_lines_glow(ax)
print(np.unique(train_final_preds, return_counts=True))
print(roc_auc_score(train_df[target], train_final_preds))
plt.show()

In [ ]:
train_submission = pd.DataFrame(data={'id': train_df.index, target[0]: train_final_preds})
train_submission.to_csv(fr'rendered_data/{objective}_train_submission.csv', index=False)

test_submission = pd.DataFrame(data={'id': test_df.index, target[0]: test_final_preds})
test_submission.to_csv(fr'rendered_data/{objective}_test_submission.csv', index=False)